In [7]:
"""
This training script can be run both on a single gpu in debug mode,
and also in a larger training run with distributed data parallel (ddp).

To run on a single GPU, example:
$ python train.py --batch_size=32 --compile=False

To run with DDP on 4 gpus on 1 node, example:
$ torchrun --standalone --nproc_per_node=4 train.py

To run with DDP on 4 gpus across 2 nodes, example:
- Run on the first (master) node with example IP 123.456.123.456:
$ torchrun --nproc_per_node=8 --nnodes=2 --node_rank=0 --master_addr=123.456.123.456 --master_port=1234 train.py
- Run on the worker node:
$ torchrun --nproc_per_node=8 --nnodes=2 --node_rank=1 --master_addr=123.456.123.456 --master_port=1234 train.py
(If your cluster does not have Infiniband interconnect prepend NCCL_IB_DISABLE=1)
"""

import os
import time
import math
import pickle
import json
from contextlib import nullcontext

import pandas as pd

import numpy as np
import torch
from torch.nn.parallel import DistributedDataParallel as DDP
from torch.distributed import init_process_group, destroy_process_group

from model import GPTConfig, GPT

# -----------------------------------------------------------------------------
# default config values designed to train a gpt2 (124M) on OpenWebText
# I/O
out_dir = 'out-stock'
eval_interval = 100
log_interval = 1
eval_iters = 2
eval_only = False # if True, script exits right after the first eval
always_save_checkpoint = False # if True, always save a checkpoint after each eval
init_from = 'scratch' # 'scratch' or 'resume' or 'gpt2*'
# wandb logging
wandb_log = False # disabled by default
wandb_project = 'stock'
wandb_run_name = 'mini-gpt' # 'run' + str(time.time())
# data
dataset = 'stock'
gradient_accumulation_steps = 1 # used to simulate larger batch sizes
batch_size = 12 # if gradient_accumulation_steps > 1, this is the micro-batch size
block_size = 5
# model
n_layer = 8
n_head = 8
n_embd = 512 # 参数估计：params= layer*(12*emb**2), 数据量估计dataSize= 10 *params
# dropout = 0.998728434 # for pretraining 0 is good, for finetuning try 0.1+
dropout = 0
# dropout = 1-dataSize/10/params
bias = False # do we use bias inside LayerNorm and Linear layers?
meta_vocab_size = n_embd // 2

# adamw optimizer
learning_rate = 1e-3 # max learning rate
max_iters = 1e6 # total number of training iterations
weight_decay = 1e-1
beta1 = 0.9
beta2 = 0.99
grad_clip = 1.0 # clip gradients at this value, or disable if == 0.0
# learning rate decay settings
decay_lr = True # whether to decay the learning rate
warmup_iters = 100 # how many steps to warm up for
lr_decay_iters = 2000 # should be ~= max_iters per Chinchilla
min_lr = 1e-4 # minimum learning rate, should be ~= learning_rate/10 per Chinchilla

# system
device = 'cpu' # examples: 'cpu', 'cuda', 'cuda:0', 'cuda:1' etc., or try 'mps' on macbooks
dtype = 'float16' # 'float32', 'bfloat16', or 'float16', the latter will auto implement a GradScaler
# -----------------------------------------------------------------------------
config_keys = [k for k,v in globals().items() if not k.startswith('_') and isinstance(v, (int, float, bool, str))]
config = {k: globals()[k] for k in config_keys} # will be useful for logging
# -----------------------------------------------------------------------------

master_process = True
seed_offset = 0


if master_process:
    os.makedirs(out_dir, exist_ok=True)
torch.manual_seed(1337 + seed_offset)
torch.backends.cuda.matmul.allow_tf32 = True # allow tf32 on matmul
torch.backends.cudnn.allow_tf32 = True # allow tf32 on cudnn
device_type = 'cuda' if 'cuda' in device else 'cpu' # for later use in torch.autocast
# note: float16 data type will automatically use a GradScaler
ptdtype = {'float32': torch.float32, 'bfloat16': torch.bfloat16, 'float16': torch.float16}[dtype]
ctx = nullcontext() if device_type == 'cpu' else torch.amp.autocast(device_type=device_type, dtype=ptdtype)


In [8]:
np.random.seed(42)

datadir = os.path.join('data', dataset)

# meta数据
meta = {}
with open(os.path.join(datadir, 'meta.pkl'), 'r') as f:
    meta = json.load(f)
    meta_vocab_size = meta['vocab_size']
    meta_vocab_size = 4096
def decode(id):
    return meta['itos'][str(id)]
def encode(s):
    return [meta['stoi'][c] for c in s]

pd_train_data = pd.read_csv(os.path.join(datadir, 'train.csv')).iloc[1:,:meta_vocab_size+1]
pd_val_data = pd.read_csv(os.path.join(datadir, 'val.csv')).iloc[:,:meta_vocab_size+1]
pd_val_data



trade_date  000001.SZ  000002.SZ  000004.SZ  000005.SZ  000006.SZ  \
0     20240219     1.0145     0.9781     1.0800     0.9565     0.9852   
1     20240220     1.0010     1.0061     1.0144     1.0455     1.0025   
2     20240221     1.0998     1.0313     1.0218     1.0435     1.0100   
3     20240222     1.0093     0.9941     1.0455     1.0556     0.9975   
4     20240223     0.9954     1.0049     1.0586     1.0526     1.0099   
5     20240226     0.9705     0.9784     1.0335     1.0500     0.9902   
6     20240227     0.9972     1.0080     1.0998     1.0476     1.0248   
7     20240228     0.9990     0.9871     0.8997     1.0455     0.9661   
8     20240229     1.0095     1.0111     1.0246     1.0543     1.0175   
9     20240301     0.9906     0.9851     1.0232     0.9485     1.0222   
10    20240304     0.9847     0.9535     1.0242     0.9457     0.9663   
11    20240305     1.0097     1.0053     0.9618     0.9540     0.9875   
12    20240306     0.9904     0.9842     1.1000  -100.0000     0.9949   
13    20240307     1.0048     0.9871     0.9459  -100.0000     1.0102   
14    20240308     1.0000     0.9967     1.0114  -100.0000     0.9950   
15    20240311     1.0087     1.0305     1.0271  -100.0000     1.0101   
16    20240312     1.0086     1.0571     1.0022  -100.0000     1.0275   
17    20240313     0.9782     0.9690     1.0132  -100.0000     0.9732   
18    20240314     0.9903     1.0021     1.0998  -100.0000     1.0000   
19    20240315     1.0362     0.9753     1.0434  -100.0000     1.0025   
20    20240318     0.9943     0.9968     0.9842  -100.0000     1.0025   
21    20240319     0.9867     0.9883     0.9718  -100.0000     0.9876   
22    20240320     1.0048     1.0032     0.9947  -100.0000     1.0050   
23    20240321     1.0019     1.0043     0.9854  -100.0000     1.0025   
24    20240322     0.9895     0.9851     0.9785  -100.0000     0.9850   
25    20240325     1.0039     1.0086     1.0027  -100.0000     0.9822   
26    20240326     1.0192     1.0128     1.0137  -100.0000     1.0233   
27    20240327     0.9934     0.9736     0.9912  -100.0000     0.9697   
28    20240328     0.9962     1.0033     1.0532  -100.0000     1.0104   
29    20240329     1.0029     0.9740     0.9741  -100.0000     1.0180   

    000007.SZ  000008.SZ  000009.SZ  000010.SZ  ...  603320.SH  603321.SH  \
0      1.0149     1.0145     0.9950     1.0359  ...     1.0999     1.0534   
1      1.0490     0.9952     1.0000     1.0396  ...     1.0306     1.0127   
2      1.0023     1.0096     0.9858     1.0429  ...     1.0248     1.0233   
3      0.9837     1.0047     1.0102     1.0137  ...     1.0502     1.0385   
4      0.9763     1.0142     0.9992     1.0450  ...     1.0524     1.0589   
5      1.0267     1.0047     0.9941     1.0216  ...     1.0315     1.0795   
6      0.9953     1.0093     1.0101     1.0127  ...     1.0347     1.0103   
7      0.9501     0.9679     0.9757     0.9250  ...     0.9001     0.9242   
8      0.9950     1.0190     1.0206     1.0586  ...     1.0155     1.0268   
9      0.9874     1.0047     1.0101     0.9830  ...     1.0036     0.9923   
10     0.9847     0.9954     0.9750     0.9913  ...     0.9920     0.9876   
11     1.0491     0.9907     0.9770     0.9782  ...     0.9820     0.9781   
12     1.0271     1.0000     1.0026     1.0625  ...     1.0357     1.0176   
13     0.9928     1.0986     0.9843     0.9664  ...     1.0301     1.0110   
14     1.0217     1.0983     1.0000     0.9913  ...     0.9888     1.0062   
15     1.0496     1.1012     1.0469     1.0351  ...     1.0287     1.0170   
16     0.9865     1.0247     0.9873     1.0169  ...     1.0135     1.0076   
17     0.9932     0.9241     0.9803     0.9958  ...     1.0092     1.0106   
18     1.0069     1.0821     0.9852     1.0084  ...     0.9992     0.9925   
19     1.0046     0.9483     1.0160     1.0166  ...     1.0157     1.0211   
20     0.9955     1.0109     0.9974     1.0082  ...     1.0317     1.0310   
21     1.0320     0.9820     0.9904     0.9919

In [9]:
def trans_frame_to_id(dataframe):
    train_data = dataframe.iloc[:, 1:]
    # 对所有行，都取前10个最大的
    def top_n(row, n):
        # return row.nlargest(n).values
        return row.nlargest(n).index.tolist()

    n = 20
    data_top_10 = train_data.apply(top_n, axis=1, n=n)

    # 将结果转换为 [266, 10] 的形状
    data_transformed = pd.DataFrame(data_top_10.tolist(), index=train_data.index)

    def to_id(row):
        return encode(row)
    
    data_transformed = data_transformed.apply(to_id, axis=1)
    data_transformed = torch.stack([torch.tensor(row) for row in data_transformed])
    return data_transformed

train_data = trans_frame_to_id(pd_train_data)
val_data = trans_frame_to_id(pd_val_data)

print(f'train.shape is {train_data.shape}')


train.shape is torch.Size([269, 20])


In [10]:
# 写个python程序，从pandas数据中获取一批训练数据：
# 1. 读取pandas数据A，格式是：[trade_date, label1, label2, label3，。。。]，date的样例有：20230104，label*是数字，样例有1.0399、0.9943
# 2. X是生成指定格式的shape = [shape, ]

import random

random.seed(42)
torch.manual_seed(33)

def print_data_info(split, index_data, index_id):
    data = pd_train_data if split == 'train' else pd_val_data
    data = pd_train_data

    print(f'{split}, code is {decode(index_id)}, date is {data.iloc[index_data, 0]},price_chg is {data.iloc[index_data, (index_id+1)*2]}, aount_chg is {data.iloc[index_data, (index_id+1)*2-1]}')


def get_batch(split):
    data = train_data if split == 'train' else val_data
    # data = val_data

    indices = torch.randint(len(data)-1-block_size, (batch_size, ))

    # (batch, block)
    x = torch.stack([data[i:i+block_size] for i in indices])
    x = x.gather(2, torch.randint(x.shape[2], (x.shape[0], x.shape[1], 1))).squeeze(-1)

    # (batch, block)
    y = torch.stack([data[i+1:i+1+block_size] for i in indices])
    y = y.gather(2, torch.randint(y.shape[2], (y.shape[0], y.shape[1], 1))).squeeze(-1)

    # index = indices[0].item()
    # print(f'index is {index}, raw_data is {data[index:index+block_size+1]}')
    # print(f'get train_data x is {x[0]}, y is {y[0]}')
    # print(f'get train_data_src x is {[decode(i.item()) for i in x[0]]}, y is {y[0]}')

    return x, y

get_batch('val')



(tensor([[2142,  816, 2262, 2750, 1923],
         [3367, 2446, 2484, 2394, 2344],
         [1648, 2413, 2807, 1780, 1780],
         [2807,  690, 1889, 2417, 1946],
         [1205, 2197, 2807, 2026, 2375],
         [ 535, 2633, 3723, 1961, 2110],
         [1822, 1648, 1601, 2270, 2599],
         [2110, 2496, 2582, 2839, 3525],
         [2512, 3510, 2534, 1684, 2306],
         [2502, 2477, 3937, 1946, 2200],
         [2817, 2518, 2747, 2249, 1563],
         [2077, 2750, 2523, 2362,  724]]),
 tensor([[1771, 3060, 2750, 2197,  789],
         [1901, 2184, 1702, 1780, 2142],
         [1976, 1517, 1889, 2764, 2366],
         [2833, 2142, 2023, 2384, 1889],
         [2681, 2362, 1318, 1907, 3367],
         [2519, 2579, 2502, 3222, 2249],
         [1534, 2357, 2728, 2681, 2333],
         [2357, 1656, 1517, 3937, 2446],
         [1676,  120, 2597, 2352,  505],
         [2839, 2819, 1901, 2484, 2180],
         [1115, 2713, 1762, 1676, 2206],
         [2217, 2431, 1931,  141, 2681]]))

In [11]:
# init these up here, can override if init_from='resume' (i.e. from a checkpoint)
iter_num = 0
best_val_loss = 1e9

# model init
model_args = dict(n_layer=n_layer, n_head=n_head, n_embd=n_embd, block_size=block_size,
                  bias=bias, vocab_size=meta_vocab_size, dropout=dropout) # start with model_args from command line
if init_from == 'scratch':
    # init a new model from scratch
    print("Initializing a new model from scratch")
    gptconf = GPTConfig(**model_args)
    model = GPT(gptconf)


model.to(device)

# initialize a GradScaler. If enabled=False scaler is a no-op
scaler = torch.cuda.amp.GradScaler(enabled=(dtype == 'float16'))

# optimizer
optimizer = model.configure_optimizers(weight_decay, learning_rate, (beta1, beta2), device_type)

checkpoint = None # free up memory



# helps estimate an arbitrarily accurate loss over either split using many batches
@torch.no_grad()
def estimate_loss():
    out = {}
    model.eval()
    for split in ['train', 'val']:
        losses = torch.zeros(eval_iters)
        for k in range(eval_iters):
            X, Y = get_batch(split)
            with ctx:
                logits, loss = model(X, Y)
            losses[k] = loss.item()
        out[split] = losses.mean()
    model.train()
    return out

# learning rate decay scheduler (cosine with warmup)
def get_lr(it):
    # 1) linear warmup for warmup_iters steps
    if it < warmup_iters:
        return learning_rate * it / warmup_iters
    # 2) if it > lr_decay_iters, return min learning rate
    if it > lr_decay_iters:
        return min_lr
    # 3) in between, use cosine decay down to min learning rate
    decay_ratio = (it - warmup_iters) / (lr_decay_iters - warmup_iters)
    assert 0 <= decay_ratio <= 1
    coeff = 0.5 * (1.0 + math.cos(math.pi * decay_ratio)) # coeff ranges 0..1
    return min_lr + coeff * (learning_rate - min_lr)

# logging
if wandb_log and master_process:
    import wandb
    wandb.init(project=wandb_project, name=wandb_run_name, config=config)

X, Y = get_batch('train')

# 遍历并打印模型中的所有权重参数
# for name, param in model.named_parameters():
#     print(f"{name}: {param.shape}, {param}")

print(f'X is {X}')
print(f'Y is {Y}')
logits, loss = model(X, Y)
print(logits.shape)
# print(f'logits is {logits}, shape is {logits.shape}')
# print(f'loss is {loss}, loss.shape is {loss.shape}')


# print(model)


Initializing a new model from scratch
config is GPTConfig(block_size=5, vocab_size=4096, n_layer=8, n_head=8, n_embd=512, dropout=0, bias=False)
number of parameters: 27.27M
num decayed parameter tensors: 34, with 27,265,536 parameters
num non-decayed parameter tensors: 17, with 8,704 parameters
using fused AdamW: False
X is tensor([[2421, 1985, 2047, 2551, 2073],
        [1286, 1708, 1545, 2302, 1968],
        [3329, 2893, 2906, 3329, 4022],
        [2438,  464, 1159, 1339,  710],
        [2067, 2444,  361, 1057,   81],
        [2061,    8, 3299,  741, 1208],
        [2150, 2421, 2887, 1985, 1904],
        [1361, 1004, 2774, 3870, 1136],
        [2994,  789, 1500, 1148,  872],
        [2493,  220,  925, 2377, 2097],
        [2107,  848, 2076, 3597,   98],
        [2198, 1649, 2433, 2635, 2015]])
Y is tensor([[2101, 1933, 2551, 3879, 2003],
        [1708, 2941, 2726,  680, 2311],
        [2906,  355, 3954, 1374, 2803],
        [3326, 2395, 2210, 3923,  375],
        [ 237, 1361,  750, 

/Users/renyabin/opt/anaconda3/envs/nanogpt/lib/python3.8/site-packages/torch/cuda/amp/grad_scaler.py:126: UserWarning: torch.cuda.amp.GradScaler is enabled, but CUDA is not available.  Disabling.
  warnings.warn(


In [12]:


# training loop
# X, Y = get_batch('train') # fetch the very first batch
t0 = time.time()
local_iter_num = 0 # number of iterations in the lifetime of this process
raw_model = model # unwrap DDP container if needed
running_mfu = -1.0
while True:
    # evaluate the loss on train/val sets and write checkpoints
    if iter_num % eval_interval == 0 and master_process:
        losses = estimate_loss()
        print(f"step {iter_num}: train loss {losses['train']:.4f}, val loss {losses['val']:.4f}")
        
        if losses['val'] < best_val_loss or always_save_checkpoint:
            best_val_loss = losses['val']
            if iter_num > 0:
                checkpoint = {
                    'model': raw_model.state_dict(),
                    'optimizer': optimizer.state_dict(),
                    'model_args': model_args,
                    'iter_num': iter_num,
                    'best_val_loss': best_val_loss,
                    'config': config,
                }
                print(f"saving checkpoint to {out_dir}")
                torch.save(checkpoint, os.path.join(out_dir, 'ckpt.pt'))
                
    if iter_num == 0 and eval_only:
        break
    
    X, Y = get_batch('train')
    logits, loss = model(X, Y)

    optimizer.zero_grad()
    loss.backward()

    optimizer.step()

    # timing and logging
    t1 = time.time()
    dt = t1 - t0
    t0 = t1
    if iter_num % log_interval == 0 and master_process:
        # get loss as float. note: this is a CPU-GPU sync point
        # scale up to undo the division above, approximating the true total loss (exact would have been a sum)
        lossf = loss.item() * gradient_accumulation_steps
        if local_iter_num >= 5: # let the training loop settle a bit
            mfu = raw_model.estimate_mfu(batch_size * gradient_accumulation_steps, dt)
            running_mfu = mfu if running_mfu == -1.0 else 0.9*running_mfu + 0.1*mfu
        print(f"iter {iter_num}: loss {lossf:.4f}, time {dt*1000:.2f}ms, mfu {running_mfu*100:.2f}%")
    iter_num += 1
    local_iter_num += 1

    # termination conditions
    if iter_num > max_iters:
        break



step 0: train loss 8.4129, val loss 8.3681
iter 0: loss 8.4344, time 1074.66ms, mfu -100.00%
iter 1: loss 8.3966, time 346.81ms, mfu -100.00%
iter 2: loss 8.2723, time 329.78ms, mfu -100.00%
iter 3: loss 8.4188, time 336.03ms, mfu -100.00%
iter 4: loss 8.3593, time 329.69ms, mfu -100.00%
iter 5: loss 8.4136, time 344.17ms, mfu 0.01%
iter 6: loss 8.3932, time 320.27ms, mfu 0.01%
iter 7: loss 8.3233, time 321.61ms, mfu 0.01%
iter 8: loss 8.3715, time 317.63ms, mfu 0.01%
iter 9: loss 8.0155, time 310.63ms, mfu 0.01%
iter 10: loss 8.1728, time 311.89ms, mfu 0.01%
iter 11: loss 8.1790, time 313.42ms, mfu 0.01%
iter 12: loss 8.2294, time 315.51ms, mfu 0.01%
iter 13: loss 8.1385, time 314.65ms, mfu 0.01%
iter 14: loss 8.2557, time 309.94ms, mfu 0.01%
iter 15: loss 8.1873, time 312.70ms, mfu 0.01%
iter 16: loss 8.1589, time 310.61ms, mfu 0.01%
iter 17: loss 8.3818, time 310.34ms, mfu 0.01%
iter 18: loss 8.3860, time 311.18ms, mfu 0.01%
iter 19: loss 8.2294, time 311.85ms, mfu 0.01%
iter 20: lo

KeyboardInterrupt: 